In [1]:
#!pip install lime
#!pip install shap
#!pip install anchor-exp
#!pip install hyperopt
#!pip install imodels

import pandas as pd
import numpy as np

import xgboost as xgb

import pickle

from imodels import BayesianRuleListClassifier
from collections import OrderedDict

from sklearn.model_selection import train_test_split, GridSearchCV, RandomizedSearchCV
from sklearn.metrics import accuracy_score, roc_auc_score, classification_report, mean_squared_error, mean_absolute_error, mean_absolute_percentage_error
from sklearn.preprocessing import LabelBinarizer, StandardScaler,MinMaxScaler
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor 
from sklearn.linear_model import LogisticRegression, LinearRegression
from sklearn.neighbors import KNeighborsClassifier, KNeighborsRegressor
from sklearn.naive_bayes import GaussianNB

import os
import joblib

import warnings
warnings.filterwarnings('ignore')

import matplotlib.pyplot as plt

from matplotlib.pyplot import figure
import matplotlib.image as mpimg
import pylab as pl
from pylab import savefig
plt.style.use('seaborn-deep')

import stability as st

import statistics
import scipy as scp
import math

import lime
import lime.lime_tabular

import shap

from anchor import anchor_tabular

import time
import random

C:\ProgramData\Anaconda3\lib\site-packages\numpy\_distributor_init.py:30: UserWarning: loaded more than 1 DLL from .libs:
C:\ProgramData\Anaconda3\lib\site-packages\numpy\.libs\libopenblas.NOIJJG62EMASZI6NYURL6JBKM4EVBGM7.gfortran-win_amd64.dll
C:\ProgramData\Anaconda3\lib\site-packages\numpy\.libs\libopenblas.XWYDX2IKJW2NMTWSFYNGFUWKQU3LYTCZ.gfortran-win_amd64.dll
  warnings.warn("loaded more than 1 DLL from .libs:"


In [2]:
# path to project folder
# please change to your own
PATH = os.getcwd()

dataset = "bike_sharing"
cls_method = "decision_tree" 

classification = False

random_state = 39
num_eval = 500
n_splits = 3
random.seed(random_state)

save_to = "%s/%s/" % (PATH, dataset)
dataset_folder = "%s/datasets/" % (save_to)

In [3]:
#Get datasets
X_train = pd.read_csv(dataset_folder+dataset+"_Xtrain.csv", index_col=False, sep = ";")#.values
X_test = pd.read_csv(dataset_folder+dataset+"_Xtest.csv", index_col=False, sep = ";")#.values
X_validation = pd.read_csv(dataset_folder+dataset+"_Xvalidation.csv", index_col=False, sep = ";")#.values

y_train = pd.read_csv(dataset_folder+dataset+"_Ytrain.csv", index_col=False, sep = ";").values.reshape(-1)
y_test = pd.read_csv(dataset_folder+dataset+"_Ytest.csv", index_col=False, sep = ";").values.reshape(-1)
y_validation = pd.read_csv(dataset_folder+dataset+"_Yvalidation.csv", index_col=False, sep = ";").values.reshape(-1)

#cat_values = pd.read_csv(dataset_folder+"/cat_cols.csv").columns

feat_list = X_train.columns
results_template = pd.read_csv(os.path.join(dataset_folder, dataset+"_results_template.csv"), index_col=False)

In [4]:
results_template

Actual
0         39
1         89
2         45
3         55
4        176
...      ...
5209     243
5210      16
5211     154
5212     410
5213     323

[5214 rows x 1 columns]

In [5]:
#Set hyperparameter grid
if cls_method == "xgboost":
    space = {'learning_rate': [random.uniform(0,5) for i in range(5)],
            'subsample': [random.uniform(0.5,1) for i in range(5)],
            'max_depth': np.arange(1, 33, 6),
            'colsample_bytree': [random.uniform(0,1) for i in range(5)],
            'min_child_weight': np.arange(0,6,1)}
    fit_params = {"eval_set": [(X_train, y_train)]}
    
elif cls_method == "decision_tree":
    space = {"splitter": ["best", "random"],
            "min_samples_split": [random.uniform(0, 1) for i in range (50)],
            "max_features": [random.uniform(0,1) for i in range (50)]}
    fit_params = {"sample_weight": None}
    
elif cls_method == "logit":
    space = {"fit_intercept": [True, False],
             "penalty": ['l1', 'l2', 'elasticnet', 'none'],
             "max_iter": [random.uniform(5,200) for i in range (50)],
             "tol": np.logspace(-4, 4, 50)}
    fit_params = {"sample_weight": None}
    
elif cls_method == "brl":
    space = {"minsupport": [random.uniform(0.1,0.9) for i in range (5)],
             "max_iter": [random.randint(10000, 50000) for i in range(3)],
             "maxcardinality": [random.randint(2, 10) for i in range((3))],
             "n_chains": [random.randint(1,7) for i in range(3)]}
    
    feature_dict = OrderedDict()
    
    for i in range(len(feat_list)):
        feature_dict[feat_list[i]] = f'X_{i}'
    #cat_features = [feature_dict[value] for value in cat_values]
    
    #X_train[cat_values] = X_train[cat_values].astype(str)
        
    fit_params = {"feature_names": feat_list}
                 #'undiscretized_features': cat_features}
    
elif cls_method == "lin_reg":
    space = {"fit_intercept": [True, False]}
    fit_params = {"sample_weight": None}

elif cls_method == "knn":
    space = {'n_neighbors': [random.randint(1, 15) for i in range(10)],
             'weights': ['uniform', 'distance'],
             'leaf_size': [random.randint(1,30) for i in range(10)],
             'p': [1,2],
             'algorithm': ['kd_tree', 'ball_tree', 'brute']}
    fit_params = {}

elif cls_method == "nb":
    space = {'var_smoothing': np.logspace(0, -9, 100)}
    fit_params = {}

In [6]:
#X_train['is_recid'].values

In [7]:
#Create prediction model
if classification == True:
    if cls_method == "xgboost":
        estimator = xgb.XGBClassifier(random_state = random_state)
    elif cls_method == "decision_tree":
        space["criterion"] = ["gini", "entropy"]
        estimator = DecisionTreeClassifier(random_state = random_state)
    elif cls_method == "logit":
        estimator = LogisticRegression(random_state = random_state)
    elif cls_method == "brl":
        estimator = BayesianRuleListClassifier(random_state = random_state)
    elif cls_method == "knn":
        estimator = KNeighborsClassifier()
    elif cls_method == "nb":
        estimator = GaussianNB()
        
else:
    if cls_method == "xgboost":
        estimator = xgb.XGBRegressor(random_state = random_state)
    elif cls_method == "decision_tree":
        space["criterion"] = ["mse", "friedman_mse", "mae", "poisson"]
        estimator = DecisionTreeRegressor(random_state = random_state)
    elif cls_method == "lin_reg":
        estimator = LinearRegression()
    elif cls_method == "knn":
        estimator = KNeighborsRegressor()
        
cls = GridSearchCV(estimator, space, verbose = 10)
cls.fit(X_train.values, y_train, **fit_params)

Fitting 5 folds for each of 5000 candidates, totalling 25000 fits
[CV 1/5; 1/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.20985124453651727, splitter=best
[CV 1/5; 1/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.20985124453651727, splitter=best;, score=0.440 total time=   0.0s
[CV 2/5; 1/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.20985124453651727, splitter=best
[CV 2/5; 1/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.20985124453651727, splitter=best;, score=0.389 total time=   0.0s
[CV 3/5; 1/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.20985124453651727, splitter=best
[CV 3/5; 1/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.20985124453651727, splitter=best;, score=0.463 total time=   0.0s
[CV 4/5; 1/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.209851

[CV 4/5; 7/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=best;, score=0.288 total time=   0.0s
[CV 5/5; 7/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=best
[CV 5/5; 7/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=best;, score=0.285 total time=   0.0s
[CV 1/5; 8/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=random
[CV 1/5; 8/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=random;, score=0.319 total time=   0.0s
[CV 2/5; 8/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=random
[CV 2/5; 8/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.3956006670655835, splitter=random;, score=0.287 total time=   0.0s
[CV 3/5

[CV 4/5; 13/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=best
[CV 4/5; 13/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=best;, score=0.435 total time=   0.0s
[CV 5/5; 13/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=best
[CV 5/5; 13/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=best;, score=0.409 total time=   0.0s
[CV 1/5; 14/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=random
[CV 1/5; 14/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=random;, score=0.365 total time=   0.0s
[CV 2/5; 14/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.25468605515889453, splitter=random
[CV 2/5; 14/5000] END crit

[CV 1/5; 21/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best
[CV 1/5; 21/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best;, score=0.314 total time=   0.0s
[CV 2/5; 21/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best
[CV 2/5; 21/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best;, score=0.330 total time=   0.0s
[CV 3/5; 21/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best
[CV 3/5; 21/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best;, score=0.351 total time=   0.0s
[CV 4/5; 21/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.29400468375380795, splitter=best
[CV 4/5; 21/5000] END criterion=

[CV 3/5; 27/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=best;, score=0.774 total time=   0.0s
[CV 4/5; 27/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=best
[CV 4/5; 27/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=best;, score=0.803 total time=   0.0s
[CV 5/5; 27/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=best
[CV 5/5; 27/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=best;, score=0.776 total time=   0.0s
[CV 1/5; 28/5000] START criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=random
[CV 1/5; 28/5000] END criterion=mse, max_features=0.7089142863784148, min_samples_split=0.00861667177051828, splitter=random;, score=0.810 total time=   0.

...

[CV 5/5; 4980/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.4238513957547625, splitter=random;, score=0.458 total time=   0.0s
[CV 1/5; 4981/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.42217723868822266, splitter=best
[CV 1/5; 4981/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.42217723868822266, splitter=best;, score=0.470 total time=   0.0s
[CV 2/5; 4981/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.42217723868822266, splitter=best
[CV 2/5; 4981/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.42217723868822266, splitter=best;, score=0.439 total time=   0.0s
[CV 3/5; 4981/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.42217723868822266, splitter=best
[CV 3/5; 4981/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.42217723868822266, split

[CV 5/5; 4986/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.8673128365846117, splitter=random;, score=0.256 total time=   0.0s
[CV 1/5; 4987/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.5133662267065129, splitter=best
[CV 1/5; 4987/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.5133662267065129, splitter=best;, score=0.423 total time=   0.0s
[CV 2/5; 4987/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.5133662267065129, splitter=best
[CV 2/5; 4987/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.5133662267065129, splitter=best;, score=0.408 total time=   0.0s
[CV 3/5; 4987/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.5133662267065129, splitter=best
[CV 3/5; 4987/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.5133662267065129, splitter=be

[CV 2/5; 4993/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitter=best;, score=0.428 total time=   0.0s
[CV 3/5; 4993/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitter=best
[CV 3/5; 4993/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitter=best;, score=0.461 total time=   0.0s
[CV 4/5; 4993/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitter=best
[CV 4/5; 4993/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitter=best;, score=0.460 total time=   0.0s
[CV 5/5; 4993/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitter=best
[CV 5/5; 4993/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.46017286502427257, splitt

[CV 1/5; 4999/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039, splitter=best;, score=0.673 total time=   0.0s
[CV 2/5; 4999/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039, splitter=best
[CV 2/5; 4999/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039, splitter=best;, score=0.664 total time=   0.0s
[CV 3/5; 4999/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039, splitter=best
[CV 3/5; 4999/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039, splitter=best;, score=0.658 total time=   0.0s
[CV 4/5; 4999/5000] START criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039, splitter=best
[CV 4/5; 4999/5000] END criterion=poisson, max_features=0.9438820146989431, min_samples_split=0.000526716743062039,

GridSearchCV(estimator=DecisionTreeRegressor(random_state=39),
             param_grid={'criterion': ['mse', 'friedman_mse', 'mae', 'poisson'],
                         'max_features': [0.7089142863784148,
                                          0.0454905826728117,
                                          0.1880252951207605,
                                          0.6196815661998339,
                                          0.6199430933667057,
                                          0.6187885012625985,
                                          0.6335643409263643,
                                          0.8008756213880013,
                                          0.9447250650000294,
                                          0.9678064605793659,
                                          0.38745912650847436...
                                               0.8146899866097305,
                                               0.29400468375380795,
                                    

In [8]:
cls = cls.best_estimator_
joblib.dump(cls, save_to+cls_method+"/cls.joblib")

if cls_method == "brl":
    print(cls)

In [9]:
test_x = pd.concat([X_test, X_validation])
test_y = np.hstack([y_test, y_validation])
if cls_method == "brl":
    y_pred = cls.predict(test_x.values, threshold = 0.5)
else:
    y_pred = cls.predict(test_x.values)

if classification == True:
    print(classification_report(test_y, y_pred))
else:
    print("RMSE:", mean_squared_error(test_y, y_pred, squared = False))
    print("MAE:", mean_absolute_error(test_y, y_pred))
    print("MAPE:", mean_absolute_percentage_error(test_y, y_pred))

RMSE: 64.09826631457318
MAE: 36.87341772151899
MAPE: 0.3937302466372699


In [10]:
if classification:
    full_test = pd.concat([test_x.reset_index(), results_template], axis = 1, join = 'inner').drop(['index'], axis = 1)
    full_test["predicted"] = y_pred
    
    grouped = full_test.groupby('predicted')
    if grouped.size().min() <= 50:
      balanced = grouped.apply(lambda x: x.sample(grouped.size().min()).reset_index(drop=True))
    else:
      balanced = grouped.apply(lambda x: x.sample(50).reset_index(drop=True))
    
    test_sample = balanced[X_test.columns]
    test_sample.reset_index(drop = True, inplace = True)
    
    results_template = balanced[results_template.columns]
    results_template.reset_index(drop = True, inplace = True)
    
    if cls_method == "brl":
        preds = cls.predict(test_sample.values, threshold = 0.5)
    else:
        preds = cls.predict(test_sample.values)
    probas = [cls.predict_proba(test_sample.values)[i][preds[i]] for i in range(len(preds))]

    results_template["Prediction"] = preds
    results_template["Prediction Probability"] = probas

In [11]:
if classification == False:
    full_test = pd.concat([test_x.reset_index(), results_template], axis = 1, join = 'inner').drop(['index'], axis = 1)
    if len(full_test) <= 100:
      sample = full_test
    else:
      sample = full_test.sample(100).reset_index(drop=True)

    test_sample = sample[X_test.columns]
    test_sample.reset_index(drop = True, inplace = True)

    results_template = sample[results_template.columns]
    results_template.reset_index(drop = True, inplace = True)
    
    preds = cls.predict(test_sample.values)
    results_template["Prediction"] = preds

In [12]:
results_template.to_csv(os.path.join(save_to, cls_method, "results.csv"), sep = ";", index = False)
test_sample.to_csv(os.path.join(save_to, cls_method, "test_sample.csv"), sep = ";", index = False)

In [13]:
results_template

Actual  Prediction
0         4         5.0
1       117       143.5
2        26        33.5
3       463       574.5
4       541       495.5
..      ...         ...
495      10        16.0
496     671       862.0
497     531       384.0
498     300       246.5
499     232       149.0

[500 rows x 2 columns]